# DAMI Eliza IMMOWEB Analysis

### Cleaning up the data

In [6]:
import folium
import pandas as pd
import plotly.graph_objs as go
import plotly.express as px
import numpy as np
import re

In [7]:
csv_file_path = '../data/clean/cleaned_row_immoweb_data0403.csv'

# Read the CSV file and create a DataFrame
df = pd.read_csv(csv_file_path)
df = df.rename_axis("id")

df = df.drop('id', axis=1)
df = df.drop_duplicates(subset=['region', 'province','district','locality','postalcode','latitude','longitude','price_main','type','subtype','heatingType','cadastralIncome','epcScores','primaryEnergyConsumption','bedrooms','surface','surfaceGood','hasGasWaterElectricityConnection','condition','facadeCount','hasKitchenSetup','isFurnished','fireplaceExists','hasSwimmingPool','terraceSurface','floodZone','gardenSurface'])

# Display the first few rows of the DataFrame
df.head()
df.shape

# # Filter rows based on the 'region' column
# df = df[df['region'].isin(regions_to_keep)]

print(df.shape)

regions_to_keep = ["Wallonie", "Flanders", "Brussels"]


# Define latitude and longitude ranges
latitude_range = (48, 51.5)
longitude_range = (2.5, 6.5)

# Filter rows based on region and latitude/longitude ranges
df = df[df['region'].isin(regions_to_keep) & 
                 (df['latitude'].between(*latitude_range)) & 
                 (df['longitude'].between(*longitude_range))]

df = df[df['subtype'].str.lower() != 'castle']

# Replace 'Antwerpen' with 'Antwerp' in the 'city' column
df['locality'] = df['locality'].replace('Antwerpen', 'Antwerp')

epc_score_groups = {
    'A++': 'A++',
    'A+': 'A+',
    'A+_A++': 'A+',
    'A_A+': 'A',
    'A': 'A',
    'B': 'B',
    'C' : 'C',
    'D': 'D',
    'F_B': 'F',
    'F_C': 'F',
    'F_E': 'F',
    'F': 'F',
    'G_C': 'G',
    'G_D': 'G',
    'G_E': 'G',
    'G_F': 'G',
    'G': 'G'
}

# Map the EPC scores to groups
df['epcScores'] = df['epcScores'].map(epc_score_groups)# Calculate price per square meter


# Print the shape of the filtered DataFrame
print(df.shape)

(76368, 28)
(62150, 28)


### How many observations and features do you have ?

* Number of observations: 62150
* Number of features: 28
* Number of HOUSE observations: 35290 (56.8%)
* Number of APARTMENTS observations: 23803 (38.3%)

In [8]:

# Calculate the number of observations (rows) and features (columns) for houses
num_observations_house = df[df['type'] == 'HOUSE'].shape[0]
num_features_house = df[df['type'] == 'HOUSE'].shape[1]

# Calculate the number of observations (rows) and features (columns) for apartments
num_observations_apartment = df[df['type'] == 'APARTMENT'].shape[0]
num_features_apartment = df[df['type'] == 'APARTMENT'].shape[1]

# Calculate the total number of observations (rows) and features (columns)
num_observations_total = df.shape[0]
num_features_total = df.shape[1]

# Calculate the percentages
percent_house = (num_observations_house / num_observations_total) * 100
percent_apartment = (num_observations_apartment / num_observations_total) * 100

# Print the total number of observations and features
print("\nTotal:")
print(f"Number of observations: {num_observations_total}")
print(f"Number of features: {num_features_total}")

# Print the number of observations and features for houses
print(f"Number of HOUSE observations: {num_observations_house} ({percent_house:.1f}%)")

# Print the number of observations and features for apartments
print(f"Number of APARTMENTS observations: {num_observations_apartment} ({percent_apartment:.1f}%)")


Total:
Number of observations: 62150
Number of features: 28
Number of HOUSE observations: 35290 (56.8%)
Number of APARTMENTS observations: 23803 (38.3%)


#### What is the proportion of missing values per column?

In [9]:
# Calculate the proportion of missing values per column
missing_proportion = df.isna().mean() * 100

# Create a DataFrame to hold the missing proportion information
missing_info_df = pd.DataFrame({
    'Total Missing': missing_proportion.round(1),
    'Missing for HOUSE': df[df['type'] == 'HOUSE'].isna().mean().round(1) * 100,
    'Missing for APARTMENT': df[df['type'] == 'APARTMENT'].isna().mean().round(1) * 100
})

# Convert the DataFrame to a string without wrapping
missing_info_str = missing_info_df.to_string(line_width=1000)

# Print the missing proportion information
print("Missing Proportion Information (rounded to 1 decimal place):")
print(missing_info_str)

Missing Proportion Information (rounded to 1 decimal place):
                                  Total Missing  Missing for HOUSE  Missing for APARTMENT
region                                      0.0                0.0                    0.0
province                                    0.0                0.0                    0.0
district                                    0.0                0.0                    0.0
locality                                    0.0                0.0                    0.0
postalcode                                  0.0                0.0                    0.0
latitude                                    0.0                0.0                    0.0
longitude                                   0.0                0.0                    0.0
price_main                                  4.9                0.0                    0.0
type                                        0.0                0.0                    0.0
subtype                                

### Which variables would you delete and why?
Everything above 70% of missing values
* APARTMENTS
    * surfaceGood
    * hasGasWaterElectricityConnection
    * gardenSurface
* HOUSES
    * terraceSurface


### What variables are most subject to outliers?

In [10]:
def plot_variable(df, column):
    # Sort values from small to big
    df_sorted = df.sort_values(by=column)
    
    # Apply filters for specific columns
    if column == 'price_main':
        df_sorted = df_sorted[df_sorted[column] <= 500000]  # Limit price_main to max 500k
    elif column == 'surface':
        df_sorted = df_sorted[df_sorted[column] <= 300]  # Limit surface to max 300m²
    elif column == 'cadastralIncome':
        df_sorted = df_sorted[df_sorted[column] <= 2000]  # Limit cadastralIncome to max 2000
    
    # Create the Plotly figure
    fig = px.histogram(df_sorted, x=column, color='type', title=f'{column} Distribution', 
                       labels={'type': 'Property Type', column: 'Value'},
                       barmode='group',
                       color_discrete_map={'HOUSE': 'DodgerBlue', 'APARTMENT': 'LimeGreen'})
    
    # Display the plot in the notebook
    fig.show()

# Define the columns you want to plot
columns_to_plot = ['region', 'province', 'price_main', 'surface', 'cadastralIncome', 'epcScores', 'hasSwimmingPool']

# Loop through each column and plot its distribution
for column in columns_to_plot:
    plot_variable(df, column)